# The Battle of Neighborhoods

## Business Problem

In this notebook We will find the optimal location for a pharmacy in the city of Seville, located at the south of Spain. 
During this process we will use data comming from different data sources like the National Statistics Institute of Spain or ESRI databases.

We will use that information along with the one provided by the Foursquare API to look for the venues around each sub-neighborhood (centroid of the sub-neighborhood) in the city of Seville, then we will identify the pharmacies next to these sub-neighborhoods (centroids) as well as the sub-neighborhoods with no pharmacies around them.

On the other hand, we will use the income per household and age in the sub-neighborhoods as well as the the services around the already existing pharmacies in them to classify the pharmacies.

Finally, we will clasify the sub-neighborhoods with no pharmacy inside them and will select these sub-neighborhoods where were the age and income conditions combined with services makes them suitable for opening a pharmacy. These conditions will be:
- More than 50% of people is over 40 years
- Average perhousehold income greater than 30K €

## Data

For the execution of this analysis we will use the folowing data:

- Demographic data: https://github.com/jomsaga/Capstone/blob/main/Sevilla_Seccion_Censal_Barrio_Distrito.csv

- Sub-neighborhood centroid data: https://github.com/jomsaga/Capstone/blob/main/Centroids.csv

- Income data: https://github.com/jomsaga/Capstone/blob/main/Renta_Media_Persona_Media_Hogar_Seccion_Censal.csv





# Analysis

## Import necesarry libraries

In [877]:
import pandas as pd
import numpy as np
import geocoder
import folium
import json
import requests
from tqdm import tqdm

## Create the dataframe

### Create dataframes from different sources (CSVs)

In [878]:
DD_url = 'https://raw.githubusercontent.com/jomsaga/Capstone/main/Sevilla_Seccion_Censal_Barrio_Distrito.csv'
C_url = 'https://raw.githubusercontent.com/jomsaga/Capstone/main/Centroids.csv'
ID_url = 'https://raw.githubusercontent.com/jomsaga/Capstone/main/Renta_Media_Persona_Media_Hogar_Seccion_Censal.csv'

In [879]:
DD_df = pd.read_csv(DD_url,delimiter=';')
C_df = pd.read_csv(C_url,delimiter=';', encoding='latin-1')
ID_df = pd.read_csv(ID_url,delimiter=r"\s+", encoding='latin-1', header=None)

In [880]:
DD_df.head()

CUSEC        Barrio       Distrito  Población_Total  H_total  M_Total  \
0  4109106023   TRIANA ESTE         Triana              821      358      463   
1  4109104028   LOS PAJAROS    Cerro Amate              795      384      411   
2  4109104033    JUAN XXIII    Cerro Amate             1156      535      621   
3  4109104035  ROCHELAMBERT    Cerro Amate             1449      676      773   
4  4109101002         FERIA  Casco Antiguo              950      449      501   

   H_00_Entre_0_y_4_años  H_01_Entre_5_y_9_años  H_02_Entre_10_y_14_años  \
0                     10                     17                       28   
1                     30                     22                       17   
2                     22                     30                       34   
3                     21                     33                       38   
4                     13                     19                       13   

   H_03_Entre_15_y_19_años  ...  M_11_Entre_55_y_59_años  \
0                       22  ...                       27   
1                       24  ...                       23   
2                       27  ...                       33   
3                       32  ...                       57   
4                       16  ...                       36   

   M_12_Entre_60_y_64_años  M_13_Entre_65_y_69_años  M_14_Entre_70_y_74_años  \
0                       31                       25                       31   
1                       30                       11                        8   
2                       34                       36                       37   
3                       30                       47                       62   
4                       27                       21                       35   

   M_15_Entre_75_y_79_años  M_16_Entre_80_y_84_años  M_17_Entre_85_y_89_años  \
0                       29                       32                     14.0   
1                        7                       10                      9.0   
2                       42                       27                     33.0   
3                       31                       29                     15.0   
4                       23                       16                      9.0   

   M_18_Entre_90_y_más_años   Shape__Area  Shape__Length  
0                      12.0   43979.91553     875.704245  
1                       1.0   60709.07520    1385.198757  
2                       7.0  102626.64890    1279.491928  
3                       6.0   78884.07910    1493.304158  
4                       7.0   77461.28052    1305.417423  

[5 rows x 46 columns]

In [881]:
C_df.head()

CUSEC                                      Barrio  \
0  4109108035                             SAN PABLO D Y E   
1  4109109010  PALACIO DE CONGRESOS URBADIEZ ENTREPUENTES   
2  4109109003                        COLORES ENTREPARQUES   
3  4109110013        SECTOR SUR LA PALMERA REINA MERCEDES   
4  4109110012        SECTOR SUR LA PALMERA REINA MERCEDES   

                  Distrito  Poblacion    Shape__Are   xcoord    ycoord  
0  San Pablo - Santa Justa        769   32050.26440 -5.95739  37.39938  
1                     Este       2208  485294.70920 -5.94065  37.40601  
2                     Este       2119  380933.18040 -5.91771  37.38841  
3    Bellavista La Palmera        647   26359.63672 -5.98599  37.35797  
4    Bellavista La Palmera       1066  482544.10130 -5.98489  37.36369

In [882]:
ID_df.head()

0        1        2     3      4      5    6        7     8  \
0  4109101001  Sevilla  sección  1001  Renta  media  por  persona  2017   
1  4109101001  Sevilla  sección  1001  Renta  media  por    hogar  2017   
2  4109101002  Sevilla  sección  1002  Renta  media  por  persona  2017   
3  4109101002  Sevilla  sección  1002  Renta  media  por    hogar  2017   
4  4109101003  Sevilla  sección  1003  Renta  media  por  persona  2017   

        9  
0  15.189  
1  35.467  
2  14.763  
3  35.431  
4  15.518

#### Remove inecesary columns

In [883]:
ID_df = ID_df[[0,9]]
columns_ID_df = ['CUSEC', 'Income [k€]']
ID_df.columns = columns_ID_df
ID_df.head()

CUSEC  Income [k€]
0  4109101001       15.189
1  4109101001       35.467
2  4109101002       14.763
3  4109101002       35.431
4  4109101003       15.518

#### Create 2 income dataframes, one for person and another per house

In [884]:
ID_df_P = ID_df[ID_df.index % 2 == 0]
ID_df_P.columns = ['CUSEC','Income_Per_Person [K€]']
ID_df_P.head()

CUSEC  Income_Per_Person [K€]
0  4109101001                  15.189
2  4109101002                  14.763
4  4109101003                  15.518
6  4109101004                  15.818
8  4109101005                  15.507

In [885]:
ID_df_H = ID_df[ID_df.index % 2 != 0]
ID_df_H.columns = ['CUSEC','Income_Per_House [K€]']
ID_df_H.head()

CUSEC  Income_Per_House [K€]
1  4109101001                 35.467
3  4109101002                 35.431
5  4109101003                 34.130
7  4109101004                 37.452
9  4109101005                 35.293

### Let's Create a single dataframe containing all the information included in the different dataframes

In [886]:
C_df.set_index('CUSEC', inplace=True)

In [887]:
DD_filtered = DD_df.drop(columns=['Barrio', 'Distrito'])
DD_filtered

CUSEC  Población_Total  H_total  M_Total  H_00_Entre_0_y_4_años  \
0    4109106023              821      358      463                     10   
1    4109104028              795      384      411                     30   
2    4109104033             1156      535      621                     22   
3    4109104035             1449      676      773                     21   
4    4109101002              950      449      501                     13   
..          ...              ...      ...      ...                    ...   
526  4109109068             1252      601      651                     18   
527  4109103007             1510      698      812                     72   
528  4109105044             1450      758      692                     44   
529  4109109069             1237      608      629                     23   
530  4109109017             1793      893      900                    142   

     H_01_Entre_5_y_9_años  H_02_Entre_10_y_14_años  H_03_Entre_15_y_19_años  \
0                       17                       28                       22   
1                       22                       17                       24   
2                       30                       34                       27   
3                       33                       38                       32   
4                       19                       13                       16   
..                     ...                      ...                      ...   
526                     27                       45                       62   
527                     44                       26                       26   
528                     47                       43                       53   
529                     42                       79                       79   
530                     60                       33                       18   

     H_04_Entre_20_y_24_años  H_05_Entre_25_y_29_años  ...  \
0                         16                       20  ...   
1                         21                       37  ...   
2                         26                       30  ...   
3                         36                       41  ...   
4                         24                       45  ...   
..                       ...                      ...  ...   
526                       67                       21  ...   
527                       14                       26  ...   
528                       47                       60  ...   
529                       35                       29  ...   
530                       11                       54  ...   

     M_11_Entre_55_y_59_años  M_12_Entre_60_y_64_años  \
0                         27                       31   
1                         23                       30   
2                         33                       34   
3                         57                       30   
4                         36                       27   
..                       ...                      ...   
526                       45                       16   
527                       39                       43   
528                       53                       50   
529                       29                       11   
530                       16                        9   

     M_13_Entre_65_y_69_años  M_14_Entre_70_y_74_años  \
0                         25                       31   
1                         11                        8   
2                         36                       37   
3                         47                       62   
4                         21                       35   
..                       ...                      ...   
526                       13                       14   
527                       35                       27   
528                       38                       33   
529                       21                        5   
530                        9                        5   

     M_15

In [888]:
df = C_df
df = df.join(ID_df_P.set_index('CUSEC'), on= df.index)
df = df.join(ID_df_H.set_index('CUSEC'), on= df.index)
df = df.join(DD_filtered.set_index('CUSEC'), on= df.index)
df.head()

Barrio  \
CUSEC                                                    
4109108035                             SAN PABLO D Y E   
4109109010  PALACIO DE CONGRESOS URBADIEZ ENTREPUENTES   
4109109003                        COLORES ENTREPARQUES   
4109110013        SECTOR SUR LA PALMERA REINA MERCEDES   
4109110012        SECTOR SUR LA PALMERA REINA MERCEDES   

                           Distrito  Poblacion    Shape__Are   xcoord  \
CUSEC                                                                   
4109108035  San Pablo - Santa Justa        769   32050.26440 -5.95739   
4109109010                     Este       2208  485294.70920 -5.94065   
4109109003                     Este       2119  380933.18040 -5.91771   
4109110013    Bellavista La Palmera        647   26359.63672 -5.98599   
4109110012    Bellavista La Palmera       1066  482544.10130 -5.98489   

              ycoord  Income_Per_Person [K€]  Income_Per_House [K€]  \
CUSEC                                                                 
4109108035  37.39938                   8.048                 19.469   
4109109010  37.40601                  15.638                 51.195   
4109109003  37.38841                  11.587                 34.827   
4109110013  37.35797                  13.765                 34.004   
4109110012  37.36369                  18.457                 53.481   

            Población_Total  H_total  ...  M_11_Entre_55_y_59_años  \
CUSEC                                 ...                            
4109108035              769      363  ...                       29   
4109109010             2208     1099  ...                      121   
4109109003             2119     1036  ...                      120   
4109110013              647      283  ...                        8   
4109110012             1066      473  ...                       38   

            M_12_Entre_60_y_64_años  M_13_Entre_65_y_69_años  \
CUSEC                                                          
4109108035                       21                       21   
4109109010                      114                       89   
4109109003                       74                       66   
4109110013                       18                       28   
4109110012                       41                       30   

            M_14_Entre_70_y_74_años  M_15_Entre_75_y_79_años  \
CUSEC                                                          
4109108035                       23                       33   
4109109010                       45                       25   
4109109003                       43                       35   
4109110013                       22                       35   
4109110012                       42                       36   

            M_16_Entre_80_y_84_años  M_17_Entre_85_y_89_años  \
CUSEC                                                          
4109108035                       21                     20.0   
4109109010                       13                      9.0   
4109109003                       10                      9.0   
4109110013                       23                     22.0   
4109110012                       23                     24.0   

            M_18_Entre_90_y_más_años   Shape__Area  Shape__Length  
CUSEC                                                              
4109108035                       6.0   32050.26440    1090.486795  
4109109010                       8.0  485294.70920    3443.731401  
4109109003                       8.0  380933.18040    3206.726561  
4109110013                      12.0   26359.63672     866.828293  
4109110012                      20.0  482544.10130    4208.913795  

[5 rows x 51 columns]

#### Reset Index and cast CUSEC field as string

In [889]:
df.reset_index(inplace = True)
df[['CUSEC']] = df[['CUSEC']].astype(str) # Converting this to string since otherwise folium will not be able to link the key on the dataframe with the dataframe
df.head()

CUSEC                                      Barrio  \
0  4109108035                             SAN PABLO D Y E   
1  4109109010  PALACIO DE CONGRESOS URBADIEZ ENTREPUENTES   
2  4109109003                        COLORES ENTREPARQUES   
3  4109110013        SECTOR SUR LA PALMERA REINA MERCEDES   
4  4109110012        SECTOR SUR LA PALMERA REINA MERCEDES   

                  Distrito  Poblacion    Shape__Are   xcoord    ycoord  \
0  San Pablo - Santa Justa        769   32050.26440 -5.95739  37.39938   
1                     Este       2208  485294.70920 -5.94065  37.40601   
2                     Este       2119  380933.18040 -5.91771  37.38841   
3    Bellavista La Palmera        647   26359.63672 -5.98599  37.35797   
4    Bellavista La Palmera       1066  482544.10130 -5.98489  37.36369   

   Income_Per_Person [K€]  Income_Per_House [K€]  Población_Total  ...  \
0                   8.048                 19.469              769  ...   
1                  15.638                 51.195             2208  ...   
2                  11.587                 34.827             2119  ...   
3                  13.765                 34.004              647  ...   
4                  18.457                 53.481             1066  ...   

   M_11_Entre_55_y_59_años  M_12_Entre_60_y_64_años  M_13_Entre_65_y_69_años  \
0                       29                       21                       21   
1                      121                      114                       89   
2                      120                       74                       66   
3                        8                       18                       28   
4                       38                       41                       30   

   M_14_Entre_70_y_74_años  M_15_Entre_75_y_79_años  M_16_Entre_80_y_84_años  \
0                       23                       33                       21   
1                       45                       25                       13   
2                       43                       35                       10   
3                       22                       35                       23   
4                       42                       36                       23   

   M_17_Entre_85_y_89_años  M_18_Entre_90_y_más_años   Shape__Area  \
0                     20.0                       6.0   32050.26440   
1                      9.0                       8.0  485294.70920   
2                      9.0                       8.0  380933.18040   
3                     22.0                      12.0   26359.63672   
4                     24.0                      20.0  482544.10130   

   Shape__Length  
0    1090.486795  
1    3443.731401  
2    3206.726561  
3     866.828293  
4    4208.913795  

[5 rows x 52 columns]

### Let's represent the dataframe information in a sub-neighborhood map

#### Income per person sub-neighborhood map

In [890]:
Seville_geo = 'https://raw.githubusercontent.com/jomsaga/Capstone/main/Sevilla_Cen_Secc_Geo.json'
Seville_popup = 'https://raw.githubusercontent.com/jomsaga/Capstone/main/Sevilla_Full.json'
json_request = requests.get(Seville_popup)
json_data = json_request.json()

# Add the income in a new column in the popup json
for i in range(len(json_data['features'])):
    for j in range(len(json_data['features'])):
        if json_data['features'][i]['properties']['CUSEC'] == int(df.iloc[j,0]):
            json_data['features'][i]['properties']['Income_Per_Person [K€]'] = df.iloc[j,7]

# create a numpy array of length 6 and has linear spacing from the minium total immigration to the maximum total immigration
threshold_scale = np.linspace(df['Income_Per_Person [K€]'].min(),
                              df['Income_Per_Person [K€]'].max(),
                              6, dtype=int)
threshold_scale = threshold_scale.tolist() # change the numpy array to a list
threshold_scale[-1] = threshold_scale[-1] + 1 # make sure that the last value of the list is greater than the maximum immigration

# let Folium determine the scale.
Seville_map = folium.Map(location=[37.3826, -5.99629], zoom_start=12)
Income_Person_Theme = folium.Choropleth(
    geo_data=Seville_geo,
    data=df,
    columns=['CUSEC','Income_Per_Person [K€]'], # Be really careful here, in order for the column to match the df, the column dtype must be an string
    key_on='feature.properties.CUSEC',
    threshold_scale=threshold_scale,
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name=' Income per person [Miles de Euros]',
    reset=True
).add_to(Seville_map)

geo_json_person = folium.GeoJson(json_data,
                          style_function = lambda x: {'weight': 0, 'fillColor': '#00000000'} , 
                          popup=folium.GeoJsonPopup(fields=['Distrito','Barrio', 'Income_Per_Person [K€]'],
                                                    aliases=['District','Neighborhood', 'Income per person [K€]']))

geo_json_person.add_to(Seville_map)


Seville_map.save('Income per person.html')    
Seville_map

#### Income per house sub-neighborhood map

In [891]:
Seville_geo = 'https://raw.githubusercontent.com/jomsaga/Capstone/main/Sevilla_Cen_Secc_Geo.json'
Seville_popup = 'https://raw.githubusercontent.com/jomsaga/Capstone/main/Sevilla_Full.json'
json_request = requests.get(Seville_popup)
json_data = json_request.json()

# Add the income in a new column in the popup json
for i in range(len(json_data['features'])):
    for j in range(len(json_data['features'])):
        if json_data['features'][i]['properties']['CUSEC'] == int(df.iloc[j,0]):
            json_data['features'][i]['properties']['Income_Per_House [K€]'] = df.iloc[j,8]

# create a numpy array of length 6 and has linear spacing from the minium total immigration to the maximum total immigration
threshold_scale = np.linspace(df['Income_Per_House [K€]'].min(),
                              df['Income_Per_House [K€]'].max(),
                              6, dtype=int)
threshold_scale = threshold_scale.tolist() # change the numpy array to a list
threshold_scale[-1] = threshold_scale[-1] + 1 # make sure that the last value of the list is greater than the maximum immigration

# let Folium determine the scale.
Seville_map = folium.Map(location=[37.3826, -5.99629], zoom_start=12)
Income_Theme = folium.Choropleth(
    geo_data=Seville_geo,
    data=df,
    columns=['CUSEC','Income_Per_House [K€]'], # Be really careful here, in order for the column to match the df, the column dtype must be an string
    key_on='feature.properties.CUSEC',
    threshold_scale=threshold_scale,
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name=' Income per house [Miles de Euros]',
    reset=True
).add_to(Seville_map)

geo_json = folium.GeoJson(json_data,
                          style_function = lambda x: {'weight': 0, 'fillColor': '#00000000'} , 
                          popup=folium.GeoJsonPopup(fields=['Distrito','Barrio', 'Income_Per_House [K€]'],
                                                    aliases=['District','Neighborhood', 'Income per house [K€]']))

geo_json.add_to(Seville_map)

Seville_map.save('Income per house.html')

Seville_map

### Let's search the pharmacies near the centroids of each sub-neighborhood

In [892]:
df.head()

CUSEC                                      Barrio  \
0  4109108035                             SAN PABLO D Y E   
1  4109109010  PALACIO DE CONGRESOS URBADIEZ ENTREPUENTES   
2  4109109003                        COLORES ENTREPARQUES   
3  4109110013        SECTOR SUR LA PALMERA REINA MERCEDES   
4  4109110012        SECTOR SUR LA PALMERA REINA MERCEDES   

                  Distrito  Poblacion    Shape__Are   xcoord    ycoord  \
0  San Pablo - Santa Justa        769   32050.26440 -5.95739  37.39938   
1                     Este       2208  485294.70920 -5.94065  37.40601   
2                     Este       2119  380933.18040 -5.91771  37.38841   
3    Bellavista La Palmera        647   26359.63672 -5.98599  37.35797   
4    Bellavista La Palmera       1066  482544.10130 -5.98489  37.36369   

   Income_Per_Person [K€]  Income_Per_House [K€]  Población_Total  ...  \
0                   8.048                 19.469              769  ...   
1                  15.638                 51.195             2208  ...   
2                  11.587                 34.827             2119  ...   
3                  13.765                 34.004              647  ...   
4                  18.457                 53.481             1066  ...   

   M_11_Entre_55_y_59_años  M_12_Entre_60_y_64_años  M_13_Entre_65_y_69_años  \
0                       29                       21                       21   
1                      121                      114                       89   
2                      120                       74                       66   
3                        8                       18                       28   
4                       38                       41                       30   

   M_14_Entre_70_y_74_años  M_15_Entre_75_y_79_años  M_16_Entre_80_y_84_años  \
0                       23                       33                       21   
1                       45                       25                       13   
2                       43                       35                       10   
3                       22                       35                       23   
4                       42                       36                       23   

   M_17_Entre_85_y_89_años  M_18_Entre_90_y_más_años   Shape__Area  \
0                     20.0                       6.0   32050.26440   
1                      9.0                       8.0  485294.70920   
2                      9.0                       8.0  380933.18040   
3                     22.0                      12.0   26359.63672   
4                     24.0                      20.0  482544.10130   

   Shape__Length  
0    1090.486795  
1    3443.731401  
2    3206.726561  
3     866.828293  
4    4208.913795  

[5 rows x 52 columns]

### Let's create a dataframe containing all pharmacies in each sub-neighborhood

In [893]:
CLIENT_ID = 'UZZCI3GU0B0TESGPPWWGIL1UFKAB1NKJ2QGF0W0VEAZBLGUH' #'XZ00IYHHH1TQXGJPE44J24KGX2L00I4M4QNZ2QX3DSDWDUTN'
CLIENT_SECRET = 'YN03BGN2GZCZBTQH4ANJVVKSMLUH350ON0BLPRSNWHZ4UZAE' #'B0UT2Q1ZKYGGXQYSNW2EIR2ZMJQL1THI2UMQ2N2VR4XBKWZK'
VERSION = '20180605'
LIMIT = 100
RADIUS = 500 
QUERY = 'Farmacia'

In [859]:
pharmacy_df_list = []

for sub_neighborhood, neighborhood, district, lat, lng in tqdm(zip(df['CUSEC'], df['Barrio'], df['Distrito'], df['ycoord'], df['xcoord'])):
    LATITUDE = lat
    LONGITUDE = lng
    
    url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'.format(
    CLIENT_ID,
    CLIENT_SECRET,
    LATITUDE,
    LONGITUDE,
    VERSION,
    QUERY,
    RADIUS,
    LIMIT)
    
    results = requests.get(url).json()
    
    for venue in range(len(results['response']['venues'])):
        name = results['response']['venues'][venue]['name']
        pharmacy_lat = results['response']['venues'][venue]['location']['lat']
        pharmacy_lng = results['response']['venues'][venue]['location']['lng']
        distance = results['response']['venues'][venue]['location']['distance']
        
        pharmacy_df_list.append((district, neighborhood, sub_neighborhood, name, distance, pharmacy_lat, pharmacy_lng))

columns = ['District','Neighborhood','Sub-neighborhood','Pharmacy_Name','Distance[m]','Latitude','Longitude']
pharmacy_df = pd.DataFrame(pharmacy_df_list)
pharmacy_df.columns = columns
    

531it [02:47,  3.16it/s]


In [894]:
pharmacy_df.head()

District                                Neighborhood  \
0  San Pablo - Santa Justa                             SAN PABLO D Y E   
1  San Pablo - Santa Justa                             SAN PABLO D Y E   
2  San Pablo - Santa Justa                             SAN PABLO D Y E   
3                     Este  PALACIO DE CONGRESOS URBADIEZ ENTREPUENTES   
4                     Este  PALACIO DE CONGRESOS URBADIEZ ENTREPUENTES   

  Sub-neighborhood                                   Pharmacy_Name  \
0       4109108035                               Farmacia Gran Vía   
1       4109108035                           Farmacia c/ Jerusalen   
2       4109108035                              Farmacia San Pablo   
3       4109109010         Farmacia Lda. Mª. Carmen Garzón Álvarez   
4       4109109010  Farmacia Licenciado Juan J. Rodríguez Villalba   

   Distance[m]   Latitude  Longitude  
0          455  37.403376  -5.956255  
1          578  37.394608  -5.959976  
2          620  37.394352  -5.960430  
3          152  37.407375  -5.940567  
4          425  37.406590  -5.935897

#### Let's Clean the dataframe, let's remove invalid venues

### Let's represent all the pharmacies in a map

In [895]:
Seville_Pharmacy_Map = folium.Map(location=[37.3826, -5.99629], zoom_start=12)

for lat, lng, district, neighborhood, sub_neighborhood, pharmacy_name in zip(pharmacy_df['Latitude'],
                                                                             pharmacy_df['Longitude'],
                                                                             pharmacy_df['District'],
                                                                             pharmacy_df['Neighborhood'],
                                                                             pharmacy_df['Sub-neighborhood'],
                                                                             pharmacy_df['Pharmacy_Name']):
    
    label = 'District: {}, Neighborhood: {}, Sub-neighborhood: {}, Pharmacy: {}'.format(district,
                                                                                      neighborhood,
                                                                                      sub_neighborhood,
                                                                                      pharmacy_name)
    
    label = folium.Popup(label, parse_html=True)
    
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(Seville_Pharmacy_Map)  

Seville_Pharmacy_Map.save('Pharmacy.html')

Seville_Pharmacy_Map